SBOM Research Project 


**Any cell with a Date and Time indicates that the Code is workin and is finalized**

In [35]:
#Same training model but with a TQDM bar for tracking progress
#Revert back to the previous code if this does not work as intended


#Used this to create CVEmodel.pkl (which is working) : Date = 25-08-2024 : 3:52 pm

import os
import json
import pandas as pd
from tqdm import tqdm  # Import tqdm for progress bars

def prepare_dataset(data_dir):
    records = []
    files_list = []
    
    # Collect all JSON files
    for root, _, files in os.walk(data_dir):
        for file in files:
            if file.endswith('.json'):
                files_list.append(os.path.join(root, file))
    
    # Initialize tqdm progress bar
    for file in tqdm(files_list, desc="Processing files", unit="file"):
        with open(file, 'r') as f:
            data = json.load(f)
            
            # Safely extract CVE ID
            cve_id = data.get('cveMetadata', {}).get('cveId', 'Unknown CVE ID')
            
            # Safely extract description
            description_data = data.get('description', {})
            description = description_data.get('value', '') if isinstance(description_data, dict) else ''
            
            # Safely extract metrics
            metrics_data = data.get('metrics', [])
            metrics = []
            for metric in metrics_data:
                for key, value in metric.items():
                    metrics.append(value)
            
            # Convert metrics to a JSON string if not empty
            metrics_json = json.dumps(metrics) if metrics else '[]'
            
            # Safely extract cveMetadata
            cve_metadata = data.get('cveMetadata', {})
            
            # Append record
            records.append({
                'cveId': cve_id,
                'description': description,
                'metrics': metrics_json,
                'cveMetadata': cve_metadata
            })
    
    return pd.DataFrame(records)

# Example usage
data_dir = r'C:\Users\immanuel\Desktop\Trial'
df = prepare_dataset(data_dir)

# Combine description and metrics for features
df['features'] = df['description'] + " " + df['metrics']

# Save the model and data together again
import joblib
model_save_path = './CVEmodel.pkl'
joblib.dump({'model': pipeline, 'data': df.to_dict()}, model_save_path)


Processing files: 100%|██████████| 258177/258177 [20:03<00:00, 214.60file/s] 


['./CVEmodel.pkl']

In [4]:
#This code is used to return the metrics, description and the metadata
#This is the final code which is working

#Date : 25-08-2024 : 3:52 PM


import joblib
import pandas as pd

def load_data(file_path):
    return joblib.load(file_path)

def predict_cve_info(cve_id, df):
    if 'cveId' not in df.columns:
        raise KeyError("'cveId' column is missing in the DataFrame.")
    
    record = df[df['cveId'] == cve_id]
    if not record.empty:
        description = record['description'].values[0]
        metrics = record['metrics'].values[0]
        cve_metadata = record['cveMetadata'].values[0]
        return {
            'description': description,
            'metrics': metrics,
            'cveMetadata': cve_metadata
        }
    else:
        return None

# Load the pre-processed data
data_file = 'CVEmodel.pkl'
data = load_data(data_file)
df = pd.DataFrame(data['data'])  # Convert the dictionary back to a DataFrame

# Example CVE ID to lookup
cve_id_input = 'CVE-2024-2004'  # Replace with the CVE ID to look up
cve_info_prediction = predict_cve_info(cve_id_input, df)

if cve_info_prediction:
    print(f"Description:\n{cve_info_prediction['description']}")
    print(f"Metrics:\n{cve_info_prediction['metrics']}")
    print(f"CVE Metadata:\n{cve_info_prediction['cveMetadata']}")
else:
    print(f"No information available for CVE ID: {cve_id_input}")


Description:
An issue was found in the CPython `tempfile.TemporaryDirectory` class affecting versions 3.12.1, 3.11.7, 3.10.13, 3.9.18, and 3.8.18 and prior.

The tempfile.TemporaryDirectory class would dereference symlinks during cleanup of permissions-related errors. This means users which can run privileged programs are potentially able to modify permissions of files referenced by symlinks in some circumstances.

Metrics:
[{"attackComplexity": "HIGH", "attackVector": "LOCAL", "availabilityImpact": "NONE", "baseScore": 7.8, "baseSeverity": "HIGH", "confidentialityImpact": "HIGH", "integrityImpact": "HIGH", "privilegesRequired": "NONE", "scope": "CHANGED", "userInteraction": "NONE", "vectorString": "CVSS:3.1/AV:L/AC:H/PR:N/UI:N/S:C/C:H/I:H/A:N", "version": "3.1"}, "CVSS", [{"lang": "en", "value": "GENERAL"}], {"type": "ssvc", "content": {"id": "CVE-2023-6597", "role": "CISA Coordinator", "options": [{"Exploitation": "none"}, {"Automatable": "no"}, {"Technical Impact": "partial"}], "ver

---


Try to integrate the SBOM file along with the CVE Information Code

In [2]:
#Extracts all the cveId values from a given SBOM file

#Date = 25-08-2024 : 4:25 PM

import json

def extract_cve_ids(file_path):
    try:
        # Load the JSON data from the file with explicit encoding
        with open(file_path, 'r', encoding='utf-8') as file:
            data = json.load(file)
        
        # Extract the list of vulnerabilities
        vulnerabilities = data.get('vulnerabilities', [])
        
        # Extract the 'id' from each vulnerability
        cve_ids = [vuln.get('id') for vuln in vulnerabilities if 'id' in vuln]
        
        return cve_ids
    
    except UnicodeDecodeError as e:
        print(f"UnicodeDecodeError: {e}")
    except json.JSONDecodeError as e:
        print(f"JSONDecodeError: {e}")
    except Exception as e:
        print(f"An error occurred: {e}")

# Replace 'your_file.json' with the path to your JSON file
file_path = r'C:\Users\immanuel\Desktop\projekt\Research Project\SBOM\amazonlinuxcyclonedx.json'
cve_ids = extract_cve_ids(file_path)

# Print or use the list of CVE ids
if cve_ids:
    print(cve_ids)


['CVE-2023-6597', 'CVE-2024-0450', 'CVE-2024-2004', 'CVE-2024-2398', 'CVE-2024-28182', 'CVE-2024-2961']


In [27]:
#This code iterates through the found cveId values and creates a json file with all the information
#Only issues is that the JSON file is not that readable.

#Date = 25-08-2024 : 4:25 PM

import joblib
import pandas as pd
import json

def load_data(file_path):
    """Load data from a pickle file."""
    return joblib.load(file_path)

def prepare_lookup_dict(df):
    """Convert DataFrame to a dictionary for faster lookups."""
    lookup_dict = df.set_index('cveId').to_dict(orient='index')
    print("Available CVE IDs:", lookup_dict.keys())  # Debugging line
    return lookup_dict

def predict_cve_info(cve_id, lookup_dict):
    """Predict and retrieve CVE information based on cve_id."""
    record = lookup_dict.get(cve_id, None)
    if record:
        return {
            'description': record['description'],
            'metrics': record['metrics'],
            'cveMetadata': record['cveMetadata']
        }
    else:
        print(f"CVE ID '{cve_id}' not found in the lookup dictionary.")  # Debugging line
        return None

def process_cve_files(cve_files, lookup_dict):
    """Process an array of CVE file names and return a dictionary of CVE information."""
    cve_info = {}
    for cve_id in cve_files:
        info = predict_cve_info(cve_id, lookup_dict)
        if info:
            cve_info[cve_id] = info
        else:
            cve_info[cve_id] = "No information available"
    return cve_info

def save_to_json(data, output_file):
    """Save data to a JSON file."""
    with open(output_file, 'w') as f:
        json.dump(data, f, indent=4)

# Load the pre-processed data
data_file = 'CVEmodel.pkl'
data = load_data(data_file)

# Convert the dictionary back to a DataFrame
df = pd.DataFrame(data['data'])

# Prepare lookup dictionary
lookup_dict = prepare_lookup_dict(df)

# Process CVE files and get their information
cve_info = process_cve_files(cve_ids , lookup_dict)

# Save the results to a JSON file
output_file = 'cveFinal.json'
save_to_json(cve_info, output_file)

print(f"Results have been saved to {output_file}")


Available CVE IDs: dict_keys(['CVE-1999-0001', 'CVE-1999-0002', 'CVE-1999-0003', 'CVE-1999-0004', 'CVE-1999-0005', 'CVE-1999-0006', 'CVE-1999-0007', 'CVE-1999-0008', 'CVE-1999-0009', 'CVE-1999-0010', 'CVE-1999-0011', 'CVE-1999-0012', 'CVE-1999-0013', 'CVE-1999-0014', 'CVE-1999-0015', 'CVE-1999-0016', 'CVE-1999-0017', 'CVE-1999-0018', 'CVE-1999-0019', 'CVE-1999-0020', 'CVE-1999-0021', 'CVE-1999-0022', 'CVE-1999-0023', 'CVE-1999-0024', 'CVE-1999-0025', 'CVE-1999-0026', 'CVE-1999-0027', 'CVE-1999-0028', 'CVE-1999-0029', 'CVE-1999-0030', 'CVE-1999-0031', 'CVE-1999-0032', 'CVE-1999-0033', 'CVE-1999-0034', 'CVE-1999-0035', 'CVE-1999-0036', 'CVE-1999-0037', 'CVE-1999-0038', 'CVE-1999-0039', 'CVE-1999-0040', 'CVE-1999-0041', 'CVE-1999-0042', 'CVE-1999-0043', 'CVE-1999-0044', 'CVE-1999-0045', 'CVE-1999-0046', 'CVE-1999-0047', 'CVE-1999-0048', 'CVE-1999-0049', 'CVE-1999-0050', 'CVE-1999-0051', 'CVE-1999-0052', 'CVE-1999-0053', 'CVE-1999-0054', 'CVE-1999-0055', 'CVE-1999-0056', 'CVE-1999-0057', '

In [28]:
import json
import ast

def fix_metrics_field(metrics_str):
    # Use ast.literal_eval to safely evaluate the JSON string
    try:
        # Replace escaped newline characters with actual newlines
        fixed_metrics_str = metrics_str.replace('\\n', '\n').replace('\\"', '"')
        return json.loads(fixed_metrics_str)  # Convert the string to a JSON object
    except json.JSONDecodeError as e:
        print(f"Error decoding metrics: {e}")
        return None

def process_cve_data(input_file, output_file):
    with open(input_file, 'r') as file:
        raw_data = file.read()
    
    try:
        data = json.loads(raw_data)
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON: {e}")
        return

    for cve_id, cve_info in data.items():
        if 'metrics' in cve_info:
            # Fix the 'metrics' field
            cve_info['metrics'] = fix_metrics_field(cve_info['metrics'])

    with open(output_file, 'w') as file:
        json.dump(data, file, indent=4, sort_keys=True)

# Specify the input and output file names
input_file = 'cveFinal.json'
output_file = 'fixed_cve_data.json'

process_cve_data(input_file, output_file)


--- 
Test for integrating and automating the process of extracting cveIds, creating a JSON file and making it readable

In [ ]:
#Automation process of the code

#Date = 25-08-2024 : 4:25 PM

import joblib
import pandas as pd
import json
import os

def load_data(file_path):
    """Load data from a pickle file."""
    return joblib.load(file_path)

def prepare_lookup_dict(df):
    """Convert DataFrame to a dictionary for faster lookups."""
    lookup_dict = df.set_index('cveId').to_dict(orient='index')
    return lookup_dict

def predict_cve_info(cve_id, lookup_dict):
    """Predict and retrieve CVE information based on cve_id."""
    record = lookup_dict.get(cve_id, None)
    if record:
        return {
            'description': record['description'],
            'metrics': record['metrics'],
            'cveMetadata': record['cveMetadata']
        }
    else:
        return None

def process_cve_files(cve_files, lookup_dict):
    """Process an array of CVE file names and return a dictionary of CVE information."""
    cve_info = {}
    for cve_id in cve_files:
        info = predict_cve_info(cve_id, lookup_dict)
        if info:
            cve_info[cve_id] = info
        else:
            cve_info[cve_id] = "No information available"
    return cve_info

def save_to_json(data, output_file):
    """Save data to a JSON file."""
    with open(output_file, 'w') as f:
        json.dump(data, f, indent=4)

print("Creating file.... Please wait\n(Takes less than a minute)")

# Load the pre-processed data
data_file = 'CVEmodel.pkl'
data = load_data(data_file)

# Convert the dictionary back to a DataFrame
df = pd.DataFrame(data['data'])

# Prepare lookup dictionary
lookup_dict = prepare_lookup_dict(df)

# Process CVE files and get their information
cve_info = process_cve_files(cve_ids, lookup_dict)

# Save the results to a JSON file
cveSavedFile = 'cveFinal.json'
save_to_json(cve_info, cveSavedFile)

#Code past this is for making the JSON file readable

def fix_metrics_field(metrics_str):
    # Use ast.literal_eval to safely evaluate the JSON string
    try:
        # Replace escaped newline characters with actual newlines
        fixed_metrics_str = metrics_str.replace('\\n', '\n').replace('\\"', '"')
        return json.loads(fixed_metrics_str)  # Convert the string to a JSON object
    except json.JSONDecodeError as e:
        print(f"Error decoding metrics: {e}")
        return None

def process_cve_data(input_file, output_file):
    with open(input_file, 'r') as file:
        raw_data = file.read()
    
    try:
        data = json.loads(raw_data)
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON: {e}")
        return

    for cve_id, cve_info in data.items():
        if 'metrics' in cve_info:
            # Fix the 'metrics' field
            cve_info['metrics'] = fix_metrics_field(cve_info['metrics'])

    with open(output_file, 'w') as file:
        json.dump(data, file, indent=4, sort_keys=True)


output_file = 'cveData.json'
process_cve_data(cveSavedFile , output_file)
os.remove(cveSavedFile)  # Delete the file
print("\n\nFile created at ",os.path.abspath(output_file))

---
Test to integrate full project. Request user for SBOM file path -> Extract the CVE Ids and create an array -> Get information of each CVE ID
-> Create a JSON file 

In [30]:
#Date = 25-08-2024 : 5:03 PM

import joblib
import pandas as pd
import json
import os

def extract_cve_ids(file_path):
        # Load the JSON data from the file with explicit encoding
        with open(file_path, 'r', encoding='utf-8') as file:
            data = json.load(file)
        # Extract the list of vulnerabilities
        vulnerabilities = data.get('vulnerabilities', [])
        # Extract the 'id' from each vulnerability
        cve_ids = [vuln.get('id') for vuln in vulnerabilities if 'id' in vuln]
        return cve_ids

def load_data(file_path):
    """Load data from a pickle file."""
    return joblib.load(file_path)

def prepare_lookup_dict(df):
    """Convert DataFrame to a dictionary for faster lookups."""
    lookup_dict = df.set_index('cveId').to_dict(orient='index')
    return lookup_dict

def predict_cve_info(cve_id, lookup_dict):
    """Predict and retrieve CVE information based on cve_id."""
    record = lookup_dict.get(cve_id, None)
    if record:
        return {
            'description': record['description'],
            'metrics': record['metrics'],
            'cveMetadata': record['cveMetadata']
        }
    else:
        return None

def process_cve_files(cve_files, lookup_dict):
    """Process an array of CVE file names and return a dictionary of CVE information."""
    cve_info = {}
    for cve_id in cve_files:
        info = predict_cve_info(cve_id, lookup_dict)
        if info:
            cve_info[cve_id] = info
        else:
            cve_info[cve_id] = "No information available"
    return cve_info

def save_to_json(data, output_file):
    """Save data to a JSON file."""
    with open(output_file, 'w') as f:
        json.dump(data, f, indent=4)

def fix_metrics_field(metrics_str):
    # Use ast.literal_eval to safely evaluate the JSON string
    try:
        # Replace escaped newline characters with actual newlines
        fixed_metrics_str = metrics_str.replace('\\n', '\n').replace('\\"', '"')
        return json.loads(fixed_metrics_str)  # Convert the string to a JSON object
    except json.JSONDecodeError as e:
        print(f"Error decoding metrics: {e}")
        return None

def process_cve_data(input_file, output_file):
    with open(input_file, 'r') as file:
        raw_data = file.read()
    
    try:
        data = json.loads(raw_data)
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON: {e}")
        return

    for cve_id, cve_info in data.items():
        if 'metrics' in cve_info:
            # Fix the 'metrics' field
            cve_info['metrics'] = fix_metrics_field(cve_info['metrics'])

    with open(output_file, 'w') as file:
        json.dump(data, file, indent=4, sort_keys=True)
        

file_path = r'C:\Users\immanuel\Desktop\projekt\Research\SBOM\amazonlinuxcyclonedx.json'
cve_ids = extract_cve_ids(file_path)
# Print or use the list of CVE ids
if not cve_ids :
    print("No CVE Ids found in the following SBOM file")

print("Creating file...\nThe file creation process should take less than a minute, or almost a minute at most, depending on your system's performance.")

# Load the pre-processed data
data_file = 'CVEmodel.pkl'
data = load_data(data_file)

# Convert the dictionary back to a DataFrame
df = pd.DataFrame(data['data'])

# Prepare lookup dictionary
lookup_dict = prepare_lookup_dict(df)

# Process CVE files and get their information
cve_info = process_cve_files(cve_ids, lookup_dict)

# Save the results to a JSON file
cveSavedFile = 'cveFinal.json'
save_to_json(cve_info, cveSavedFile)

output_file = 'cveData.json'
process_cve_data(cveSavedFile , output_file)
os.remove(cveSavedFile)  # Delete the file
print("\n\nFile created at ",os.path.abspath(output_file))


Creating file...
The file creation process should take less than a minute, or almost a minute at most, depending on your system's performance.


File created at  c:\Users\immanuel\Desktop\projekt\Research\SBOM\cveData.json
